---

<h2 style="text-align: center;"><b>PyTorch. Основы: синтаксис, torch.cuda и torch.autograd</b></h2>

---

<p style="align: center;"><img src="https://upload.wikimedia.org/wikipedia/commons/9/96/Pytorch_logo.png" width=500 height=400></p>

На этом занятии мы рассмотрим основы фреймворка глубокого обучения PyTorch.  

Когда хочется написать какую-нибудь нейросеть, решающую определённую задачу, будь то какая-нибудь простая классификация чего-либо или обнаружение лиц людей на видео. Всё, конечно, всегда начинается со **сбора данных**, а уже потом реализуются модели и проводятся эксперименты.  

Однако люди быстро поняли, что писать свои нейронные сети каждый раз с нуля ну очень уж долго и неразумно, поэтому придумали так называемые **фреймворки** - модули, в которых есть функционал, с помощью которого можно быстро и просто решать типовые задачи, и уже с помощью этих средств писать решения к более сложным задачам.

Есть много различных фремворков глубокого обучения. Разница между ними прежде всего в том, каков общий принцип вычислений. 
Например, в **Caffe и Caffe2** вы пишете код, по сути, составляя его из готовых "кусочков", как в Lego, в **TensorFlow и Theano** вы сначала объявляете вычислительный граф, потом компилируете его и запускаете (sees.run()), в то время как в **Torch и PyTorch** вы пишете почти точно так же, как на NumPy, а граф вычислений создаётся только при запуске (то есть существует только во время выполнения, потом он "разрушается"). **Keras** позволяет как строить блоки, так и компилировать свой граф:

<p style="align: center;"><img src="https://habrastorage.org/web/e3e/c3e/b78/e3ec3eb78d714a7993a6b922911c0866.png" width=500 height=500></p>  
<p style="text-align: center;"><i>Картинка взята из этой [статьи на Хабре](https://habr.com/post/334380/)</i><p>

<h3 style="text-align: center;"><b>Установка</b></h3>

Инструкция по установке PyTorch есть на [официальном сайте PyTorch](https://pytorch.org/).

<h3 style="text-align: center;">Синтаксис<b></b></h3>

In [71]:
import torch

Сначала немного фактов про PyTorch:  
- динамический граф вычислений
- удобные модули `torch.nn` и `torchvision` для написания нейросетей с минимальными усилиями
- в некоторых задачах даже быстрее TensorFlow
- легко проводить вычисления на GPU

Если PyTorch представить формулой, то она будет такой:  

$$PyTorch = NumPy + CUDA + Autograd$$

(CUDA - [wiki](https://ru.wikipedia.org/wiki/CUDA))

Посмотрим, как в PyTorch выполняются операции с векторами.  

Напоминание: **тензором** называется многомерный вектор, то есть:  

x = np.array([1,2,3]) - вектор = тензор размерности 1 (то есть (1,))  
y = np.array([[1, 2, 3], [4, 5, 6]]) - матрица = тензор размерности 2 (в данном случае тензор (2, 3))  
z = np.array([[[1, 2, 3], [4, 5, 6], [7, 8, 9]],  
    [[1, 2, 3], [4, 5, 6], [7, 8, 9]],  
              [[1, 2, 3], [4, 5, 6], [7, 8, 9]]]) - "кубик" (3, 3, 3) = тензор размерности 3 (в данном случае (3, 3, 3))

Простейшим примером 3-мерного тензора является **картинка** - это "параллелепипед" из чисел, у которого три размерности - высота, ширина и количество каналов, значит это тензор размерности 3.

Понятие тензора нужно знать потому, что в PyTorch мы оперируем переменными типа `torch.Tensor` (`FloatTensor`, `IntTensor`, `ByteTensor`), и пугаться их названий совершенно не нужно - это просто векторы, у которых несколько размерностей.

Все типы тензоров:

In [73]:
torch.HalfTensor      # 16 бит, с плавающей точкой
torch.FloatTensor     # 32 бита,  с плавающей точкой
torch.DoubleTensor    # 64 бита, с плавающей точкой

torch.ShortTensor     # 16 бит, целочисленный, знаковый
torch.IntTensor       # 32 бита, целочисленный, знаковый
torch.LongTensor      # 64 бита, целочисленный, знаковый

torch.CharTensor      # 8 бит, целочисленный, знаковый
torch.ByteTensor      # 8 бит, целочисленный, беззнаковый

torch.ByteTensor

Мы будем использовать только `torch.FloatTensor()` и `torch.IntTensor()`. 

Перейдём к делу:

* Создание тензоров:

In [74]:
a = torch.FloatTensor([1, 2])
a

tensor([1., 2.])

In [75]:
a.shape

torch.Size([2])

In [76]:
b = torch.FloatTensor([[1,2,3], [4,5,6]])
b

tensor([[1., 2., 3.],
        [4., 5., 6.]])

In [77]:
b.shape

torch.Size([2, 3])

In [78]:
x = torch.FloatTensor(2,3,4)

In [79]:
x

tensor([[[-7.5219e-19,  6.8804e-43,  7.0065e-44,  0.0000e+00],
         [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00],
         [ 0.0000e+00,  0.0000e+00,  1.8754e+28,  6.4978e-07]],

        [[ 8.4336e-07,  1.0424e-11,  2.1258e+20,  1.0681e-05],
         [ 6.7003e-10,  1.6132e-07,  8.5405e+20,  2.0431e+20],
         [ 4.0292e-11,  7.1450e+31,  1.6534e+19,  3.0854e+32]]])

In [80]:
x = torch.FloatTensor(100)
x

tensor([   nan,    nan, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000])

In [81]:
x = torch.IntTensor(45, 57, 14, 2)
x.shape

torch.Size([45, 57, 14, 2])

**Обратите внимание** - если вы создаёте тензор через задание размерностей (как в примере выше), то он изначально заполняюстя случайным "мусором". Что инициализировать нулями, нужно написать .zero_() в конце:

In [82]:
x = torch.IntTensor(3, 2, 4)
x

tensor([[[-1587672904,         491,          64,           0],
         [          0,           0,           0,           0]],

        [[          0,           0,  1681143862,   926180914],
         [ 1630613554,   845504824,   912405604,   912668720]],

        [[  959461687,   946092342,   929247537,   895694948],
         [  842294628,   858863156,   845570404,  1667522869]]],
       dtype=torch.int32)

In [83]:
x = torch.IntTensor(3, 2, 4).zero_()
x

tensor([[[0, 0, 0, 0],
         [0, 0, 0, 0]],

        [[0, 0, 0, 0],
         [0, 0, 0, 0]],

        [[0, 0, 0, 0],
         [0, 0, 0, 0]]], dtype=torch.int32)

Аналог функции `np.reshape()` == `torch.view()`:

In [84]:
b.view(3, 2)

tensor([[1., 2.],
        [3., 4.],
        [5., 6.]])

In [85]:
b

tensor([[1., 2., 3.],
        [4., 5., 6.]])

**Обратите внимание** - torch.view() создаёт новый тензор, а не изменяет старый!

In [86]:
b.view(-1)

tensor([1., 2., 3., 4., 5., 6.])

In [87]:
b

tensor([[1., 2., 3.],
        [4., 5., 6.]])

* Изменение типа тензора:

In [17]:
a = torch.FloatTensor([1.5, 3.2, -7])

In [18]:
a.type_as(torch.IntTensor())

tensor([ 1,  3, -7], dtype=torch.int32)

In [19]:
a.type_as(torch.ByteTensor())

tensor([  1,   3, 249], dtype=torch.uint8)

Обратите внимание, что при `.type_as()` создаётся новый тензор (старый не меняется), то есть это не in-place операция:

In [20]:
a

tensor([ 1.5000,  3.2000, -7.0000])

* Индексация точная такая же, как и в NumPy:

In [21]:
a = torch.FloatTensor([[100, 20, 35], [15, 163, 534], [52, 90, 66]])
a

tensor([[100.,  20.,  35.],
        [ 15., 163., 534.],
        [ 52.,  90.,  66.]])

In [22]:
a[0, 0]

tensor(100.)

In [23]:
a[0][0]

tensor(100.)

In [24]:
a[0:2, 0:2]

tensor([[100.,  20.],
        [ 15., 163.]])

**Арифметика и булевы операции** работаю также, как и в NumPy, **НО** лучше использовать не опреаторы `+`, `-`, `*`, `/`, а их аналоги:  

| Оператор | Аналог |
|:-:|:-:|
|`+`| `torch.add()` |
|`-`| `torch.sub()` |
|`*`| `torch.mul()` |
|`/`| `torch.div()` |

* Сложение:

In [88]:
a = torch.FloatTensor([[1, 2, 3], [10, 20, 30], [100, 200, 300]])
b = torch.FloatTensor([[-1, -2, -3], [-10, -20, -30], [100, 200, 300]])

In [89]:
a + b

tensor([[  0.,   0.,   0.],
        [  0.,   0.,   0.],
        [200., 400., 600.]])

Лучше:

In [90]:
a.add(b)

tensor([[  0.,   0.,   0.],
        [  0.,   0.,   0.],
        [200., 400., 600.]])

In [91]:
b = -a
b

tensor([[  -1.,   -2.,   -3.],
        [ -10.,  -20.,  -30.],
        [-100., -200., -300.]])

In [92]:
a + b

tensor([[0., 0., 0.],
        [0., 0., 0.],
        [0., 0., 0.]])

* Вычитание:

In [93]:
a - b

tensor([[  2.,   4.,   6.],
        [ 20.,  40.,  60.],
        [200., 400., 600.]])

Лучше:

In [94]:
a.sub(b)

tensor([[  2.,   4.,   6.],
        [ 20.,  40.,  60.],
        [200., 400., 600.]])

* Умножение (поэлементное):

In [95]:
a * b

tensor([[    -1.,     -4.,     -9.],
        [  -100.,   -400.,   -900.],
        [-10000., -40000., -90000.]])

Лучше:

In [96]:
a.mul(b)

tensor([[    -1.,     -4.,     -9.],
        [  -100.,   -400.,   -900.],
        [-10000., -40000., -90000.]])

* Деление (поэлементное):

In [97]:
a = torch.FloatTensor([[1, 2, 3], [10, 20, 30], [100, 200, 300]])
b = torch.FloatTensor([[-1, -2, -3], [-10, -20, -30], [100, 200, 300]])

In [98]:
a / b

tensor([[-1., -1., -1.],
        [-1., -1., -1.],
        [ 1.,  1.,  1.]])

Лучше:

In [99]:
a.div(b)

tensor([[-1., -1., -1.],
        [-1., -1., -1.],
        [ 1.,  1.,  1.]])

Заметьте, все эти операции **не меняют исходные тензоры**, а **создают новые**:

In [100]:
a

tensor([[  1.,   2.,   3.],
        [ 10.,  20.,  30.],
        [100., 200., 300.]])

In [101]:
b

tensor([[ -1.,  -2.,  -3.],
        [-10., -20., -30.],
        [100., 200., 300.]])

* **Операторы сравнения**:

In [102]:
a = torch.FloatTensor([[1, 2, 3], [10, 20, 30], [100, 200, 300]])
b = torch.FloatTensor([[-1, -2, -3], [-10, -20, -30], [100, 200, 300]])

In [103]:
a == b

tensor([[0, 0, 0],
        [0, 0, 0],
        [1, 1, 1]], dtype=torch.uint8)

In [104]:
a != b

tensor([[1, 1, 1],
        [1, 1, 1],
        [0, 0, 0]], dtype=torch.uint8)

In [105]:
a < b

tensor([[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]], dtype=torch.uint8)

In [106]:
a > b

tensor([[1, 1, 1],
        [1, 1, 1],
        [0, 0, 0]], dtype=torch.uint8)

* **Булевы маски**:

In [107]:
a[a > b]

tensor([ 1.,  2.,  3., 10., 20., 30.])

In [108]:
b[a == b]

tensor([100., 200., 300.])

Опять же, тензоры не меняются:

In [109]:
a

tensor([[  1.,   2.,   3.],
        [ 10.,  20.,  30.],
        [100., 200., 300.]])

In [110]:
b

tensor([[ -1.,  -2.,  -3.],
        [-10., -20., -30.],
        [100., 200., 300.]])

Применение **стандартных функций** такое же, как и в numpy - поэлементное:

In [111]:
a = torch.FloatTensor([[1, 2, 3], [10, 20, 30], [100, 200, 300]])

In [112]:
a.sin()

tensor([[ 0.8415,  0.9093,  0.1411],
        [-0.5440,  0.9129, -0.9880],
        [-0.5064, -0.8733, -0.9998]])

In [113]:
torch.sin(a)

tensor([[ 0.8415,  0.9093,  0.1411],
        [-0.5440,  0.9129, -0.9880],
        [-0.5064, -0.8733, -0.9998]])

In [114]:
a.cos()

tensor([[ 0.5403, -0.4161, -0.9900],
        [-0.8391,  0.4081,  0.1543],
        [ 0.8623,  0.4872, -0.0221]])

In [115]:
a.exp()

tensor([[2.7183e+00, 7.3891e+00, 2.0086e+01],
        [2.2026e+04, 4.8517e+08, 1.0686e+13],
        [       inf,        inf,        inf]])

In [116]:
a.log()

tensor([[0.0000, 0.6931, 1.0986],
        [2.3026, 2.9957, 3.4012],
        [4.6052, 5.2983, 5.7038]])

In [117]:
b = -a
b

tensor([[  -1.,   -2.,   -3.],
        [ -10.,  -20.,  -30.],
        [-100., -200., -300.]])

In [118]:
b.abs()

tensor([[  1.,   2.,   3.],
        [ 10.,  20.,  30.],
        [100., 200., 300.]])

**Сумма, среднее, максимум, минимум**:

In [119]:
a.sum()

tensor(666.)

In [120]:
a.mean()

tensor(74.)

По осям:

In [121]:
a.sum(0)

tensor([111., 222., 333.])

In [122]:
a.sum(1)

tensor([  6.,  60., 600.])

In [123]:
a.max()

tensor(300.)

In [124]:
a.max(0)

(tensor([100., 200., 300.]), tensor([2, 2, 2]))

In [125]:
a.min()

tensor(1.)

In [126]:
a.min(0)

(tensor([1., 2., 3.]), tensor([0, 0, 0]))

Обратите внимание - второй тензор при вызове функций .max() и .min() - это индексы этих максимальных/минимальных элементов по указанной размерности (то есть в данном случае a.min() вернул (1, 2, 3) - минимумы по 0 оси (по столбцам), и их индексы по 0-ой оси (0,0,0) (номер каждого элемента в своём столбце)).

**Матричные операции:**

* Транспонирование матрицы (тензора):

In [127]:
a = torch.FloatTensor([[1, 2, 3], [10, 20, 30], [100, 200, 300]])
a

tensor([[  1.,   2.,   3.],
        [ 10.,  20.,  30.],
        [100., 200., 300.]])

In [128]:
a.t()

tensor([[  1.,  10., 100.],
        [  2.,  20., 200.],
        [  3.,  30., 300.]])

И снова - сам тензор не меняется (то есть при вызове создаётся новый):

In [129]:
a

tensor([[  1.,   2.,   3.],
        [ 10.,  20.,  30.],
        [100., 200., 300.]])

* Скалярное произведение векторов (1-мерных тензоров):

In [130]:
a = torch.FloatTensor([1, 2, 3, 4, 5, 6])
b = torch.FloatTensor([-1, -2, -4, -6, -8, -10])

In [131]:
a.dot(b)

tensor(-141.)

In [132]:
a @ b

tensor(-141.)

In [133]:
type(a)

torch.Tensor

In [134]:
type(b)

torch.Tensor

In [135]:
type(a @ b)

torch.Tensor

* Матричное умножение:

In [136]:
a = torch.FloatTensor([[1, 2, 3], [10, 20, 30], [100, 200, 300]])
b = torch.FloatTensor([[-1, -2, -3], [-10, -20, -30], [100, 200, 300]])

In [137]:
a.mm(b)

tensor([[  279.,   558.,   837.],
        [ 2790.,  5580.,  8370.],
        [27900., 55800., 83700.]])

In [138]:
a @ b

tensor([[  279.,   558.,   837.],
        [ 2790.,  5580.,  8370.],
        [27900., 55800., 83700.]])

Тензоры неизменны:

In [139]:
a

tensor([[  1.,   2.,   3.],
        [ 10.,  20.,  30.],
        [100., 200., 300.]])

In [140]:
b

tensor([[ -1.,  -2.,  -3.],
        [-10., -20., -30.],
        [100., 200., 300.]])

In [141]:
a = torch.FloatTensor([[1, 2, 3], [10, 20, 30], [100, 200, 300]])
b = torch.FloatTensor([[-1], [-10], [100]])

In [142]:
print(a.shape, b.shape)

torch.Size([3, 3]) torch.Size([3, 1])


In [143]:
a @ b

tensor([[  279.],
        [ 2790.],
        [27900.]])

Если "развернуть" тензор b просто в массив элементов (`torch.view(-1)`), умножение будет как на столбец:

In [144]:
b

tensor([[ -1.],
        [-10.],
        [100.]])

In [145]:
b.view(-1)

tensor([ -1., -10., 100.])

In [146]:
a @ b.view(-1)

tensor([  279.,  2790., 27900.])

In [147]:
a.mv(b.view(-1))

tensor([  279.,  2790., 27900.])

**Перевод из NumPy в PyTorch**:

In [148]:
import numpy as np

a = np.random.rand(3, 3)
a

array([[0.73297029, 0.0647068 , 0.95213803],
       [0.01135127, 0.69825433, 0.96293269],
       [0.87771321, 0.64451539, 0.32162612]])

In [149]:
b = torch.from_numpy(a)
b

tensor([[0.7330, 0.0647, 0.9521],
        [0.0114, 0.6983, 0.9629],
        [0.8777, 0.6445, 0.3216]], dtype=torch.float64)

**НО!** Обратите внимание - a и b в этом случае будут использовать одно и то же хранилище данных, то есть измение одного тензора будет менять и другой:

In [150]:
b -= b
b

tensor([[0., 0., 0.],
        [0., 0., 0.],
        [0., 0., 0.]], dtype=torch.float64)

In [151]:
a

array([[0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.]])

**Перевод из PyTorch в NumPy:**

In [152]:
a = torch.FloatTensor(2, 3, 4)
a

tensor([[[0., 0., 0., 0.],
         [0., 0., 0., 0.],
         [0., 0., 0., 0.]],

        [[0., 0., 0., 0.],
         [0., 0., 0., 0.],
         [0., 0., 0., 0.]]])

In [153]:
type(a)

torch.Tensor

In [154]:
x = a.numpy()
x

array([[[0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.]],

       [[0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.]]], dtype=float32)

In [155]:
x.shape

(2, 3, 4)

In [156]:
type(x)

numpy.ndarray

Напишем функцию `forward_pass(X, w)` ($w_0$ входит в $w$) для одного нейрона (с сигмоидой) с помощью PyTorch:

In [157]:
def forward_pass(X, w):
    return torch.sigmoid(X @ w)

In [159]:
X = torch.FloatTensor([[-5, 5], [2, 3], [1, -1]])
w = torch.FloatTensor([[-0.5], [2.5]])
result = forward_pass(X, w)
print('result: {}'.format(result))

result: tensor([[1.0000],
        [0.9985],
        [0.0474]])


<h3 style="text-align: center;"><a href="https://ru.wikipedia.org/wiki/CUDA">CUDA</a></h3>

[Краткое видео про то, как GPU используется в обучении нейросетей](https://www.youtube.com/watch?v=EobhK0UZm80)

Все вычисления в PyTorch можно проводить как на CPU, так и на GPU (Graphical Processing Unit) (если она у вас есть). В PyTorch переключение между ними делается очень просто, что является одной из ключевых его особенностей.

In [170]:
x = torch.FloatTensor(1024, 1024).uniform_()
x

tensor([[0.3411, 0.9390, 0.6315,  ..., 0.5529, 0.9262, 0.4085],
        [0.7098, 0.3078, 0.2261,  ..., 0.3477, 0.4198, 0.9744],
        [0.9441, 0.9007, 0.6284,  ..., 0.3763, 0.2614, 0.0571],
        ...,
        [0.2367, 0.0427, 0.3351,  ..., 0.7677, 0.6626, 0.9452],
        [0.2880, 0.0035, 0.8371,  ..., 0.5273, 0.8663, 0.1853],
        [0.5813, 0.2115, 0.8499,  ..., 0.2056, 0.5935, 0.6047]])

In [171]:
x.is_cuda

False

Переместим на GPU:

In [172]:
x = x.cuda()

In [173]:
x.is_cuda

True

In [174]:
x

tensor([[0.3411, 0.9390, 0.6315,  ..., 0.5529, 0.9262, 0.4085],
        [0.7098, 0.3078, 0.2261,  ..., 0.3477, 0.4198, 0.9744],
        [0.9441, 0.9007, 0.6284,  ..., 0.3763, 0.2614, 0.0571],
        ...,
        [0.2367, 0.0427, 0.3351,  ..., 0.7677, 0.6626, 0.9452],
        [0.2880, 0.0035, 0.8371,  ..., 0.5273, 0.8663, 0.1853],
        [0.5813, 0.2115, 0.8499,  ..., 0.2056, 0.5935, 0.6047]],
       device='cuda:0')

Перемножим две тензора на GPu и вернём результат вычисления на CPU:

In [176]:
a = torch.FloatTensor(10000, 10000).uniform_()
b = torch.FloatTensor(10000, 10000).uniform_()
c = a.cuda().mul(b.cuda()).cpu()

In [177]:
c

tensor([[0.2262, 0.1965, 0.4094,  ..., 0.0736, 0.2933, 0.1275],
        [0.1296, 0.1271, 0.4009,  ..., 0.0191, 0.0168, 0.4168],
        [0.8918, 0.0294, 0.1511,  ..., 0.8481, 0.0005, 0.0947],
        ...,
        [0.2218, 0.2828, 0.3110,  ..., 0.0599, 0.6793, 0.6230],
        [0.0466, 0.4787, 0.1043,  ..., 0.2514, 0.1290, 0.6491],
        [0.0375, 0.0251, 0.5316,  ..., 0.7669, 0.5638, 0.3338]])

In [178]:
a

tensor([[0.8050, 0.4509, 0.5789,  ..., 0.1817, 0.8211, 0.8840],
        [0.8009, 0.2267, 0.7719,  ..., 0.8452, 0.0451, 0.5779],
        [0.9509, 0.0704, 0.7669,  ..., 0.8987, 0.0028, 0.2946],
        ...,
        [0.2457, 0.8630, 0.5177,  ..., 0.3907, 0.9143, 0.6533],
        [0.8565, 0.8996, 0.1657,  ..., 0.9056, 0.6489, 0.7691],
        [0.1040, 0.4405, 0.8164,  ..., 0.9914, 0.8730, 0.4389]])

Тензоры, лежащие на CPU, и тензоры, лежащие на GPU, недоступны друг для друга:

In [180]:
a = torch.FloatTensor(10000, 10000).uniform_().cpu()
b = torch.FloatTensor(10000, 10000).uniform_().cuda()

In [181]:
a + b

RuntimeError: Expected object of type torch.FloatTensor but found type torch.cuda.FloatTensor for argument #3 'other'

Вот ещё немного про то, как можно работать с GPU:

In [182]:
x = torch.FloatTensor(5, 5, 5).uniform_()

# проверяем, есть ли CUDA (то есть NVidia GPU)
if torch.cuda.is_available():
    # так можно получить имя устройства, которое связано с CUDA
    # (полезно в случае с несколькими видеокартами)
    device = torch.device('cuda')          # CUDA-device объект
    y = torch.ones_like(x, device=device)  # создаём тензор на GPU
    x = x.to(device)                       # тут можно просто ``.to("cuda")``
    z = x + y
    print(z)
    # с помощью``.to`` можно и изменить тип при перемещении
    print(z.to("cpu", torch.double))

tensor([[[1.9693, 1.1198, 1.0172, 1.2034, 1.2875],
         [1.4131, 1.3164, 1.9345, 1.9337, 1.9572],
         [1.7345, 1.2186, 1.9105, 1.6177, 1.1420],
         [1.6490, 1.1597, 1.5847, 1.6580, 1.8715],
         [1.0228, 1.0453, 1.0512, 1.1437, 1.1437]],

        [[1.7028, 1.4623, 1.1701, 1.0893, 1.0764],
         [1.2116, 1.5412, 1.0967, 1.8721, 1.9107],
         [1.1340, 1.1484, 1.4099, 1.4459, 1.7837],
         [1.3865, 1.0431, 1.3485, 1.6199, 1.0908],
         [1.4057, 1.8685, 1.2232, 1.4738, 1.3243]],

        [[1.2735, 1.7283, 1.4247, 1.9058, 1.8978],
         [1.2789, 1.7611, 1.8657, 1.1219, 1.0049],
         [1.2962, 1.6973, 1.7559, 1.2467, 1.7554],
         [1.9915, 1.2676, 1.8824, 1.6168, 1.6185],
         [1.8360, 1.0345, 1.2038, 1.7657, 1.8525]],

        [[1.5283, 1.6573, 1.5225, 1.4269, 1.2714],
         [1.0401, 1.5209, 1.4956, 1.9208, 1.8503],
         [1.2160, 1.6476, 1.2769, 1.7877, 1.7272],
         [1.3110, 1.1294, 1.3310, 1.3048, 1.4476],
         [1.2117, 1.9958,

<h3 style="text-align: center;">Autograd<b></b></h3>

Расшифровывается как Automatic Gradients (автоматическое взятие градиентов) - собственно, из названия понятно, что это модуль PyTorch, отвечающий за взятие производных.  

Возможно, для вас это бдет шок, но PyTorch (и любой фреймворк глубокого обучения) может продифференцировать функцию практически любой сложности.

Импортируем нужный класс:

In [197]:
from torch.autograd import Variable

Идея такая: оборачиваем тензор в класс Variable(), получаем тоже тензор, но он имеет способность вычислять себе градиенты.  

Если а - тензор, обёрнутый в Variable(), то при вызове a.backward() берутся градиенты по всем переменным, от которых зависит тензор a.

**Примечание:** Если вы используете версию `pytorch 0.4.0` или более новую, то ***`torch.Tensor` позволяет брать по нему градиенты, класс `Variable()` использовать не нужно.*** (`torch.Variable()` - deprecated).

Примеры:

In [198]:
x = torch.FloatTensor(3, 1).uniform_()
y = torch.FloatTensor(3, 1).uniform_()
w = torch.FloatTensor(3, 3).uniform_() 
b = torch.FloatTensor(3, 1).uniform_()

x = Variable(x, requires_grad=True)
y = Variable(x, requires_grad=False)
w = Variable(w, requires_grad=True)
b = Variable(b, requires_grad=True)

y_pred = (w @ x).add_(b)

loss = (y_pred - y).sum()

# берём градиенты
loss.backward()

In [199]:
x.grad

tensor([[0.6708],
        [1.5246],
        [1.5356]])

In [200]:
w.grad

tensor([[0.0988, 0.3401, 0.6621],
        [0.0988, 0.3401, 0.6621],
        [0.0988, 0.3401, 0.6621]])

In [201]:
b.grad

tensor([[1.],
        [1.],
        [1.]])

In [202]:
y.grad

**Обратите внимание** - градиенты лежат в поле `.grad` у тех тензоров (Variable'ов), по которым брали эти градиенты. Градиенты **не лежат** в той Variable, от которой они брались!

Получить тензор из `Variable()` можно с помощью поля `.data`:

In [203]:
x

tensor([[0.0988],
        [0.3401],
        [0.6621]], requires_grad=True)

In [204]:
x.data

tensor([[0.0988],
        [0.3401],
        [0.6621]])

<h3 style="text-align: center;">Полезные ссылки:<b></b></h3>

*1). Статья по PyTorch (на русском): https://habr.com/post/334380/*

*2). Туториалы от самих разработчиков фреймворка: https://pytorch.org/tutorials/beginner/blitz/tensor_tutorial.html#sphx-glr-beginner-blitz-tensor-tutorial-py*

*3). Статья на arXiv о сравнении фреймворков глубокого обучения: https://arxiv.org/pdf/1511.06435.pdf*

4). *Ещё туториалы: https://github.com/yunjey/pytorch-tutorial*

*5). Сайт Facebook AI Research - отдела, который разрабатывает PyTorch и другие активно вкладывается в разработку инструментов для AI: https://facebook.ai/developers/tools*